In [227]:
-- holiday Table
-- Create the table
CREATE TABLE Holiday (
    Holiday DATE PRIMARY KEY,
    HolidayDescription VARCHAR(255)
);

-- Insert data into the table
INSERT INTO Holiday (Holiday, HolidayDescription)
VALUES
    ('2021-01-01', 'New Year''s Day'),
    ('2021-01-18', 'Martin Luther King'),
    ('2021-02-15', 'Washinton''s Birthday'),
    ('2021-04-02', 'Good Friday'),
    ('2021-07-05', 'Independence Day'),
    ('2021-09-06', 'Labor Day'),
    ('2021-11-25', 'Thanksgiving Day'),
    ('2021-12-24', 'Christmas Day');


(8 rows affected)

Total execution time: 00:00:00.342

In [228]:
select * from Holiday;

(8 rows affected)

Total execution time: 00:00:00.013

Holiday HolidayDescription 2021-01-01 New Year's Day 2021-01-18 Martin Luther King 2021-02-15 Washinton's Birthday 2021-04-02 Good Friday 2021-07-05 Independence Day 2021-09-06 Labor Day 2021-11-25 Thanksgiving Day 2021-12-24 Christmas Day

In [230]:
-- For an UPDATE query
UPDATE Holiday
SET [Holiday] = CONVERT(date, CAST(Holiday AS DATE), 101);

(8 rows affected)

Total execution time: 00:00:00.019

In [231]:
select * from Holiday;

(8 rows affected)

Total execution time: 00:00:00.005

Holiday HolidayDescription 2021-01-01 New Year's Day 2021-01-18 Martin Luther King 2021-02-15 Washinton's Birthday 2021-04-02 Good Friday 2021-07-05 Independence Day 2021-09-06 Labor Day 2021-11-25 Thanksgiving Day 2021-12-24 Christmas Day

In [234]:
ALTER PROCEDURE ManageNA
AS
BEGIN
    UPDATE StagingStockPrice
    SET
        [Open] = NULL
    WHERE 
        UPPER([Open]) LIKE '%N%';

    UPDATE dummyprice
    SET
        [High] = NULL
    WHERE 
        UPPER([High]) LIKE '%N%';

    UPDATE dummyprice
    SET
        [Low] = NULL
    WHERE 
        UPPER([Low]) LIKE '%N%';

    UPDATE dummyprice
    SET
        [Close] = NULL
    WHERE 
        UPPER([Close]) LIKE '%N%';

    UPDATE dummyprice
    SET
        [AdjClose] = NULL
    WHERE 
        UPPER([AdjClose]) LIKE '%N%';

    UPDATE dummyprice
    SET
        [Volume] = NULL
    WHERE 
        UPPER([Volume]) LIKE '%N%';
END;


Commands completed successfully.

Total execution time: 00:00:00.016

In [235]:
exec ManageNA

(3 rows affected)

(0 rows affected)

(0 rows affected)

(0 rows affected)

(0 rows affected)

(0 rows affected)

Total execution time: 00:00:00.524

In [278]:
Alter PROCEDURE ConvertBlanksToNull
AS
BEGIN
    -- Convert blank values to NULL
    UPDATE StagingStockPrice
    SET
        [High] = NULLIF([High], ''),
        [Open] = NULLIF([Open], ''),
        [Close] = NULLIF([Close], ''),
        [AdjClose] = NULLIF([AdjClose], ''),
        [Volume] = NULLIF([Volume], '')
    WHERE
        [High] = '' OR [Open] = '' OR [Close] = '' OR [AdjClose] = '' OR [Volume] = '';
END;


Commands completed successfully.

Total execution time: 00:00:00.115

In [238]:
exec ConvertBlanksToNull

(2 rows affected)

Total execution time: 00:00:00.766

In [239]:
alter PROCEDURE DeleteSingleTickerRecords
AS
BEGIN
    DELETE dp
    FROM StagingStockPrice dp
    WHERE NOT EXISTS (
        SELECT 1
        FROM StagingStockPrice
        WHERE Ticker = dp.Ticker
        HAVING COUNT(*) > 1
    );
END;


Commands completed successfully.

Total execution time: 00:00:00.010

In [240]:
exec DeleteSingleTickerRecords

(1 row affected)

Total execution time: 00:00:00.459

In [241]:
ALTER PROCEDURE ConvertDateColumn
AS
BEGIN
    UPDATE StagingStockPrice
    SET [Date] = CONVERT(VARCHAR(50), TRY_CONVERT(DATE, [Date], 101), 120)
    WHERE TRY_CONVERT(DATE, [Date], 101) IS NOT NULL;
END;


Commands completed successfully.

Total execution time: 00:00:00.092

In [242]:
exec ConvertDateColumn

(19149 rows affected)

Total execution time: 00:00:02.622

In [243]:
ALTER PROCEDURE AddMissingBusinessDates
AS
BEGIN
    DECLARE @MinDate DATE;
    DECLARE @MaxDate DATE;

    -- Get the minimum and maximum dates from the table
    SELECT @MinDate = MIN(CONVERT(varchar, [Date], 101)), @MaxDate = MAX(CONVERT(varchar, [Date], 101))
    FROM StagingStockPrice;

    -- Add missing records with required columns
    INSERT INTO StagingStockPrice
        (Ticker, [Date], [Open], [High], [Low], [Close], [Volume], [AdjClose])
    SELECT
        dp1.Ticker,
        bd.[Date],
        dp2.[Open],
        dp2.[High],
        dp2.[Low],
        dp2.[Close],
        dp2.[Volume],
        dp2.[AdjClose]
    FROM (
        SELECT DISTINCT Ticker
        FROM StagingStockPrice
    ) AS dp1
    CROSS JOIN (
        SELECT DISTINCT [Date]
        FROM StagingStockPrice
    ) AS bd
        LEFT JOIN StagingStockPrice dp2 ON dp1.Ticker = dp2.Ticker AND bd.[Date] = dp2.[Date]
    WHERE
        bd.[Date] BETWEEN @MinDate AND @MaxDate
        AND dp2.[Date] IS NULL -- No existing record for the combination
        AND DATEPART(WEEKDAY, bd.[Date]) NOT IN (1, 7) -- Not Saturday or Sunday
        AND NOT EXISTS (SELECT 1
        FROM Holiday
        WHERE Holiday = bd.[Date])
;
END;


Commands completed successfully.

Total execution time: 00:00:00.036

In [245]:
exec AddMissingBusinessDates

(0 rows affected)

Total execution time: 00:00:00.420

In [246]:
alter PROCEDURE AddMissingMonthEndRecords
AS
BEGIN
    -- Add missing month end records
    INSERT INTO StagingStockPrice (Ticker, [Date], [Open], [High], [Low], [Close], [Volume], [AdjClose])
    SELECT
        t.Ticker,
        CONVERT(DATE, CONVERT(VARCHAR(10), me.MonthEnd, 101), 101) AS [Date],
        NULL AS [Open],
        NULL AS [High],
        NULL AS [Low],
        NULL AS [Close],
        NULL AS [Volume],
        NULL AS [AdjClose]
    FROM (
        SELECT DISTINCT Ticker FROM StagingStockPrice
    ) AS t
    CROSS JOIN (
        SELECT DISTINCT DATEADD(DAY, -1, DATEADD(MONTH, DATEDIFF(MONTH, 0, [Date]) + 1, 0)) AS MonthEnd
        FROM StagingStockPrice
    ) AS me
    LEFT JOIN StagingStockPrice dp ON t.Ticker = dp.Ticker AND me.MonthEnd = dp.[Date]
    WHERE dp.[Date] IS NULL;

END;


Commands completed successfully.

Total execution time: 00:00:00.013

In [248]:
exec AddMissingMonthEndRecords

(0 rows affected)

Total execution time: 00:00:00.052

In [249]:
ALTER PROCEDURE CleanNonNumericData
AS
BEGIN
    UPDATE StagingStockPrice
    SET
        [Open] = CASE WHEN ISNUMERIC([Open]) = 1 THEN [Open] ELSE NULL END,
        [High] = CASE WHEN ISNUMERIC([High]) = 1 THEN [High] ELSE NULL END,
        [Low] = CASE WHEN ISNUMERIC([Low]) = 1 THEN [Low] ELSE NULL END,
        [Close] = CASE WHEN ISNUMERIC([Close]) = 1 THEN [Close] ELSE NULL END,
        AdjClose = CASE WHEN ISNUMERIC(AdjClose) = 1 THEN AdjClose ELSE NULL END,
        [Volume] = CASE WHEN ISNUMERIC([Volume]) = 1 THEN [Volume] ELSE NULL END
    WHERE
        ISNUMERIC([Open]) = 0
        OR ISNUMERIC([High]) = 0
        OR ISNUMERIC([Low]) = 0
        OR ISNUMERIC([Close]) = 0
        OR ISNUMERIC(AdjClose) = 0
        OR ISNUMERIC([Volume]) = 0;
END;


Commands completed successfully.

Total execution time: 00:00:00.083

In [254]:
EXEC CleanNonNumericData;


(464 rows affected)

Total execution time: 00:00:00.103

In [256]:
Alter PROCEDURE CleanScientificNumber
AS
BEGIN
    
UPDATE StagingStockPrice
SET [open] = CASE WHEN [open] LIKE '%E%' OR [open] LIKE '%e%' THEN CAST(CAST([open] AS FLOAT) AS VARCHAR(255)) ELSE [open] END,
    [high] = CASE WHEN [high] LIKE '%E%' OR [high] LIKE '%e%' THEN CAST(CAST([high] AS FLOAT) AS VARCHAR(255)) ELSE [high] END,
    [low] = CASE WHEN [low] LIKE '%E%' OR [low] LIKE '%e%' THEN CAST(CAST([low] AS FLOAT) AS VARCHAR(255)) ELSE [low] END,
    [close] = CASE WHEN [close] LIKE '%E%' OR [close] LIKE '%e%' THEN CAST(CAST([close] AS FLOAT) AS VARCHAR(255)) ELSE [close] END,
    Adjclose = CASE WHEN Adjclose LIKE '%E%' OR Adjclose LIKE '%e%' THEN CAST(CAST(Adjclose AS FLOAT) AS VARCHAR(255)) ELSE Adjclose END,
    [Volume] = CASE WHEN [Volume] LIKE '%E%' OR [Volume] LIKE '%e%' THEN CAST(CAST([Volume] AS FLOAT) AS VARCHAR(255)) ELSE [Volume] END;

END;


Commands completed successfully.

Total execution time: 00:00:00.021

In [257]:
Exec CleanScientificNumber

(19608 rows affected)

Total execution time: 00:00:01.883

In [259]:
Alter PROCEDURE FillNullsFromPreviousBusinessDate
AS
BEGIN
    -- Update NULL values with previous business day's data
    UPDATE dp
    SET
        [Open] = COALESCE(dp.[Open], prev.[Open]),
        [High] = COALESCE(dp.[High], prev.[High]),
        [Low] = COALESCE(dp.[Low], prev.[Low]),
        [Close] = COALESCE(dp.[Close], prev.[Close]),
        [Volume] = COALESCE(dp.[Volume], prev.[Volume]),
        [AdjClose] = COALESCE(dp.[AdjClose], prev.[AdjClose])
    FROM StagingStockPrice dp
    JOIN (
        SELECT
            Ticker,
            [Date],
            LAG([Open]) OVER (PARTITION BY Ticker ORDER BY [Date]) AS [Open],
            LAG([High]) OVER (PARTITION BY Ticker ORDER BY [Date]) AS [High],
            LAG([Low]) OVER (PARTITION BY Ticker ORDER BY [Date]) AS [Low],
            LAG([Close]) OVER (PARTITION BY Ticker ORDER BY [Date]) AS [Close],
            LAG([Volume]) OVER (PARTITION BY Ticker ORDER BY [Date]) AS [Volume],
            LAG([AdjClose]) OVER (PARTITION BY Ticker ORDER BY [Date]) AS [AdjClose]
        FROM StagingStockPrice
    ) prev
    ON dp.Ticker = prev.Ticker AND dp.[Date] = prev.[Date]
    WHERE dp.[Open] IS NULL OR dp.[High] IS NULL OR dp.[Low] IS NULL
        OR dp.[Close] IS NULL OR dp.[Volume] IS NULL OR dp.[AdjClose] IS NULL;
END;


Commands completed successfully.

Total execution time: 00:00:00.315

In [261]:
exec FillNullsFromPreviousBusinessDate

(0 rows affected)

Total execution time: 00:00:00.041

In [265]:
ALTER PROCEDURE LoadDataFromStagingStockPrice
AS
BEGIN
    -- Truncate SP500_Stock table to prepare for data load
    TRUNCATE TABLE SP500_Stock;

    -- Load data from dummyprice to SP500_Stock
    INSERT INTO SP500_Stock ([Date],[Open],[high],[low],[Close],[AdjClose],[volume],Ticker)
    SELECT
        CONVERT(DATE, [Date], 120),  -- 120 for 'yyyy-mm-dd' format
        CASE WHEN ISNUMERIC([open]) = 1 THEN CONVERT(DECIMAL(38, 10), [Open]) ELSE NULL END,
        CASE WHEN ISNUMERIC([High]) = 1 THEN CONVERT(DECIMAL(38, 10), [high]) ELSE NULL END,
        CASE WHEN ISNUMERIC([Low]) = 1 THEN CONVERT(DECIMAL(38, 10), [Low]) ELSE NULL END,
        CASE WHEN ISNUMERIC([close]) = 1 THEN CONVERT(DECIMAL(38, 10), [close]) ELSE NULL END,
        CASE WHEN ISNUMERIC([AdjClose]) = 1 THEN CONVERT(DECIMAL(38, 10), [adjclose]) ELSE NULL END,
        CASE WHEN ISNUMERIC([Volume]) = 1 THEN CONVERT(INT, [Volume]) ELSE NULL END,
        [Ticker]
    FROM StagingStockPrice;
End

Commands completed successfully.

Total execution time: 00:00:00.309

In [267]:
Exec LoadDataFromStagingStockPrice

(19608 rows affected)

Total execution time: 00:00:10.176

In [271]:
ALTER PROCEDURE CalculateChanges
AS
BEGIN
    UPDATE S
    SET
        DTDChange = ISNULL((S.[Close] - PrevData.PrevDTD) / PrevData.PrevDTD * 100, 0),
        MTDChange = ISNULL((S.[Close] - COALESCE(PrevData.PrevMTDFirstDay, PrevData.PrevMonthClose)) / COALESCE(PrevData.PrevMTDFirstDay, PrevData.PrevMonthClose) * 100, 0),
        QTDChange = ISNULL((S.[Close] - COALESCE(PrevData.PrevQTDFirstDay, PrevData.PrevQuarterClose)) / COALESCE(PrevData.PrevQTDFirstDay, PrevData.PrevQuarterClose) * 100, 0),
        YTDChange = ISNULL((S.[Close] - COALESCE(PrevData.PrevYTDFirstDay, PrevData.PrevYearClose)) / COALESCE(PrevData.PrevYTDFirstDay, PrevData.PrevYearClose) * 100, 0)
    FROM SP500_Stock S
    JOIN (
        SELECT
            Ticker,
            [Date],
            [Close],
            LAG([Close], 1) OVER (PARTITION BY Ticker ORDER BY [Date]) AS PrevDTD,
            LAG([Close], 1) OVER (PARTITION BY Ticker, YEAR([Date]), MONTH([Date]) ORDER BY [Date]) AS PrevMonthClose,
            LAG([Close], DATEDIFF(DAY, DATEADD(MONTH, -1, [Date]), [Date])) OVER (PARTITION BY Ticker ORDER BY [Date]) AS PrevMTDFirstDay,
            LAG([Close], DATEDIFF(DAY, DATEADD(MONTH, -3, [Date]), [Date])) OVER (PARTITION BY Ticker ORDER BY [Date]) AS PrevQTDFirstDay,
            LAG([Close], DATEDIFF(DAY, DATEADD(YEAR, -1, [Date]), [Date])) OVER (PARTITION BY Ticker ORDER BY [Date]) AS PrevYTDFirstDay,
            LAG([Close], 1) OVER (PARTITION BY Ticker, YEAR([Date]) - 1 ORDER BY [Date] DESC) AS PrevYearClose,
            LAG([Close], DATEDIFF(DAY, EOMONTH([Date], -1), [Date])) OVER (PARTITION BY Ticker ORDER BY [Date]) AS PrevMTDLastDay,
            LAG([Close], DATEDIFF(DAY, EOMONTH([Date], -3), [Date])) OVER (PARTITION BY Ticker ORDER BY [Date]) AS PrevQuarterClose,
            LAG([Close], DATEDIFF(DAY, EOMONTH([Date], -12), [Date])) OVER (PARTITION BY Ticker ORDER BY [Date]) AS PrevYTDLastDay
        FROM SP500_Stock
    ) PrevData
    ON S.Ticker = PrevData.Ticker AND S.[Date] = PrevData.[Date]
    WHERE S.[Date] >= '2021-01-04';
END;


Commands completed successfully.

Total execution time: 00:00:00.266

In [272]:
EXEC CalculateChanges

(19532 rows affected)

Total execution time: 00:00:12.432

In [273]:
alter PROCEDURE ReplaceNullsWithZero
AS
BEGIN
    UPDATE SP500_Stock
    SET 
        Low = ISNULL(Low, 0),
        [Close] = ISNULL([Close], 0),
        [Open] = ISNULL([Open], 0),
        AdjClose = ISNULL(AdjClose, 0),
        High = ISNULL(High, 0),
        [DTDChange] =  ISNULL(DTDChange, 0),
        [MTDChange] =  ISNULL(MTDChange, 0),
        [QTDChange] =  ISNULL(QTDChange, 0),
        [YTDChange] =  ISNULL(YTDChange, 0)
END;


Commands completed successfully.

Total execution time: 00:00:00.037

In [274]:
exec ReplaceNullsWithZero

(19608 rows affected)

Total execution time: 00:00:01.589

In [276]:
ALTER VIEW StockCompanyInfoView AS
SELECT
    s.[Date] AS AsOfDate,
    s.[Ticker],
    c.[Security],
    c.[GICS_Sector] AS GICSSector,
    c.[Headquarters_Location] AS HeadquarterLocation,
    c.[Founded],
    s.[Open] AS [Open],
    s.[Close] AS [Close],
    s.[DTDChange] AS DTDChange,
    s.[MTDChange] AS MTDChange,
    s.[QTDChange] AS QTDChange,
    s.[YTDChange] AS YTDChange
FROM
    [dbo].[SP500_Stock] s
JOIN
    [dbo].[SP500_Constituents] c ON s.[Ticker] = c.[Symbol];


Commands completed successfully.

Total execution time: 00:00:00.031

In [277]:
ALTER PROCEDURE [dbo].[GetStockDataBetweenDates]
    @StartDate DATE,
    @EndDate DATE
AS
BEGIN
    SELECT *
    FROM StockCompanyInfoView
    WHERE AsOfDate BETWEEN @StartDate AND @EndDate;
END;

Commands completed successfully.

Total execution time: 00:00:00.013

In [279]:
CREATE PROCEDURE Transformation
AS
BEGIN
    EXEC ManageNA;
    EXEC ConvertBlanksToNull;
    EXEC DeleteSingleTickerRecords;
    EXEC ConvertDateColumn;
    EXEC AddMissingBusinessDates;
    EXEC AddMissingMonthEndRecords;
    EXEC CleanNonNumericData;
    Exec CleanScientificNumber;
    Exec FillNullsFromPreviousBusinessDate;
    EXEC LoadDataFromStagingStockPrice;
    EXEC CalculateChanges;
    EXEC ReplaceNullsWithZero;

END;

Commands completed successfully.

Total execution time: 00:00:00.210

In [297]:
exec Transformation

(0 rows affected)

(0 rows affected)

(0 rows affected)

(0 rows affected)

(0 rows affected)

...

(0 rows affected)

(19608 rows affected)

(19532 rows affected)

(19608 rows affected)

Total execution time: 00:00:28.046

In [289]:
Alter PROCEDURE BulkPrep
AS
BEGIN
    truncate table StagingStockPrice

END;

Commands completed successfully.

Total execution time: 00:00:00.118

In [290]:
truncate table SP500_Stock

Commands completed successfully.

Total execution time: 00:00:00.050

In [298]:
select * from Sp500_Stock

(19608 rows affected)

Displaying Top 5000 rows.

Total execution time: 00:00:00.186

Date Open High Low Close AdjClose Volume Ticker DTDChange MTDChange QTDChange YTDChange 2021-04-01 57.1300010700 57.9000015300 57.0600013700 57.6500015300 56.3817482000 2759400 ADM 1.1403000000 3.2783000000 9.9561000000 0.2260000000 2021-04-05 57.9599990800 58.3100013700 57.3699989300 57.5200004600 56.2546043400 1922700 ADM -0.2255000000 2.4946000000 15.3398000000 -0.8959000000 2021-04-06 57.6399993900 58.2999992400 57.3199996900 58.0400009200 56.7631683300 2013200 ADM 0.9040000000 2.0932000000 16.3825000000 0.3457000000 2021-04-07 58.1199989300 58.4399986300 57.6599998500 57.8400001500 56.5675621000 1719800 ADM -0.3445000000 1.4380000000 15.9815000000 -0.5159000000 2021-04-08 57.6699981700 58.1599998500 57.6100006100 58.1399993900 56.8609657300 1759700 ADM 0.5186000000 -0.5813000000 16.5831000000 -0.6832000000 2021-04-09 58.4799995400 58.5999984700 57.8300018300 58.5400009200 57.2521629300 2420100 ADM 0.6879000000 2.0749000000 17.3852000000 -0.0853000000 2021-04-12 58.7999992400 58.9399986300 58.2900009200 58.5900001500 57.3010673500 1750900 ADM 0.0854000000 3.5524000000 0.0000000000 1.1917000000 2021-04-13 58.2799987800 58.3800010700 57.6500015300 57.9000015300 56.6262435900 2077200 ADM -1.1776000000 2.3329000000 0.0000000000 -1.1101000000 2021-04-14 58.0000000000 58.7500000000 57.7900009200 58.5499992400 57.2619438200 2022100 ADM 1.1226000000 2.1815000000 0.0000000000 -0.2045000000 2021-04-15 58.9900016800 59.0200004600 58.0900001500 58.6699981700 57.3793029800 1733900 ADM 0.2049000000 2.2659000000 0.0000000000 -1.3120000000 2021-04-16 59.1399993900 59.5800018300 58.6399993900 59.4500007600 58.1421470600 1819200 ADM 1.3294000000 4.0791000000 0.0000000000 0.2698000000 2021-04-19 59.6399993900 59.7400016800 58.8600006100 59.2900009200 57.9856643700 2089100 ADM -0.2691000000 6.8480000000 0.0000000000 0.9879000000 2021-04-20 59.2900009200 59.4799995400 58.2799987800 58.7099990800 57.4184227000 1473400 ADM -0.9782000000 1.9447000000 0.0000000000 -1.8719000000 2021-04-21 59.0800018300 59.9399986300 58.7500000000 59.8300018300 58.5137863200 1941200 ADM 1.9076000000 3.5838000000 0.0000000000 1.6307000000 2021-04-22 59.4599990800 59.6699981700 58.7400016800 58.8699989300 57.5749015800 2134900 ADM -1.6045000000 1.5174000000 0.0000000000 -0.9089000000 2021-04-23 59.0600013700 59.6500015300 58.6300010700 59.4099998500 58.1030197100 2148000 ADM 0.9172000000 1.7468000000 0.0000000000 -0.9503000000 2021-04-26 59.6300010700 60.7099990800 59.4799995400 59.9799995400 58.6604881300 3840700 ADM 0.9594000000 2.3724000000 0.0000000000 -2.9763000000 2021-04-27 59.8300018300 62.5099983200 59.5000000000 61.8199996900 60.4600029000 4741200 ADM 3.0676000000 6.1287000000 0.0000000000 -2.0285000000 2021-04-28 62.2999992400 63.3100013700 61.9000015300 63.0999984700 61.7118454000 3660700 ADM 2.0705000000 8.2332000000 0.0000000000 -0.7237000000 2021-04-29 63.7200012200 63.9000015300 62.8300018300 63.5600013700 62.1617279100 4124600 ADM 0.7290000000 10.0034000000 0.0000000000 0.6811000000 2021-04-30 63.4300003100 63.4300003100 62.6899986300 63.1300010700 61.7411880500 3332000 ADM -0.6765000000 9.4107000000 0.0000000000 -2.3208000000 2021-05-03 63.8600006100 64.9100036600 63.7099990800 64.6299972500 63.2081832900 3359700 ADM 2.3760000000 13.7251000000 28.0308000000 -0.7219000000 2021-05-04 64.5999984700 65.4199981700 64.4899978600 65.0999984700 63.6678504900 3015400 ADM 0.7272000000 15.3641000000 28.9619000000 -1.6616000000 2021-05-05 65.3000030500 66.2799987800 64.8399963400 66.1999969500 64.7436447100 3453100 ADM 1.6897000000 19.1504000000 31.1410000000 -0.7347000000 2021-05-06 66.5999984700 66.8600006100 65.6600036600 66.6900024400 65.2228775000 3417700 ADM 0.7401000000 19.2596000000 32.1117000000 -0.4923000000 2021-05-07 66.6299972500 67.3399963400 66.1299972500 67.0199966400 65.5456085200 2852100 ADM 0.4948000000 17.8269000000 32.9498000000 -0.9019000000 2021-05-10 67.2600021400 68.6800003100 67.2600021400 67.6299972500 66.1421890300 4003800 ADM 0.9101

In [286]:
exec transformation

(0 rows affected)

(0 rows affected)

(0 rows affected)

(0 rows affected)

(0 rows affected)

...

(0 rows affected)

(19608 rows affected)

(19532 rows affected)

(19608 rows affected)

Total execution time: 00:00:46.883